In [1]:
from flightanalysis.data.p23 import create_p23
from flightanalysis.schedule.definition import SchedDef
from flightanalysis.schedule import Schedule, Manoeuvre
from flightdata import Flight
from flightanalysis import State, Box
from flightplotting import plotsec, plotdtw
from flightanalysis.criteria.combination import Combination 
import numpy as np
np.set_printoptions(suppress=True)

from flightanalysis import Line, Loop, Spin, StallTurn, Snap
from geometry import Transformation

Parse a flight log, rotate it to the flightline and cutoff the takeoff and landing. 

In [2]:
#parse a flight, cutoff takeoff and landing
flown = State.from_flight(
    Flight.from_csv("examples/data/p23_example.csv").flying_only(), 
    Box.from_f3a_zone("examples/data/p23_box.f3a")
)[39:405]

Create a Schedule Definition using the create_p23 generator function. Use this to create a P23 Schedule and template State information. This is done at the average depth of the flown data and in the same direction.

In [3]:
wind=np.sign(flown[0].vel.x[0])
p23_def = create_p23(wind)  # wind direction used here because it makes the M go out and the fighter turn come back again, 

p23, template = p23_def.create_template(flown.pos.y.mean(), wind)

Align the template to the flight data.

In [4]:
dist, aligned = State.align(flown, template, 10)

In [5]:
from ipywidgets import widgets, interactive
import plotly.graph_objects as go

def dtwman(man):
    man=man-1
    fig = plotdtw(p23[man].get_data(aligned), p23[man].all_elements.to_list())
    display(go.FigureWidget(data=fig.data, layout=fig.layout))


widgets.interactive(dtwman, man=widgets.IntSlider(min=1, max=17, value=1, step=1))

interactive(children=(IntSlider(value=1, description='man', max=17, min=1), Output()), _dom_classes=('widget-i…

Update the schedule to match the flight

In [16]:
intended = p23.match_intention(template[0].transform, aligned)


create a new template then repeat the alignment

In [17]:
intended_template = intended.create_template(Transformation(
    aligned[0].pos,
    aligned[0].att.closest_principal()
))

dist, aligned = State.align(flown, intended_template, 10)



In [18]:
from ipywidgets import widgets, interactive
import plotly.graph_objects as go

def dtwman(man):
    man=man-1
    fig = plotdtw(p23[man].get_data(aligned), p23[man].all_elements.to_list())
    display(go.FigureWidget(data=fig.data, layout=fig.layout))


widgets.interactive(dtwman, man=widgets.IntSlider(min=1, max=17, value=1, step=1))

interactive(children=(IntSlider(value=1, description='man', max=17, min=1), Output()), _dom_classes=('widget-i…

Correct the intended inter element parameters to make a corrected shcedule and template

In [19]:

p23_def.update_defaults(intended)
corrected, corrected_template = p23_def.create_template(flown.pos.y.mean(), wind)


The intended template just follows the roll directions used in the flight. The corrected template corrects the roll directions if they do not fit a valid option defined in the manoeuvre parameters. We want the intended template to have these corrected roll directions.

In [20]:

intended = intended.copy_directions(corrected)

intended_template = intended.create_template(Transformation(
    aligned[0].pos,
    aligned[0].att.closest_principal()
))


In [21]:
from flightanalysis.criteria import Result
man=1
dgs =  p23_def[man].mps.collect(intended[man])



In [22]:
from json import dumps
from ipywidgets import widgets, interactive
from IPython.display import display, HTML
import plotly.graph_objects as go
import numpy as np
import pandas as pd


def scoreman(man, fl, intent, corr, inter, intra, el):
    man=intended[man-1]
    el=man.elements[el-1]

    transform = man.get_data(aligned)[0].transform
    results =  p23_def[man.uid].mps.collect(man)

    intra_results = man.analyse(
        man.get_data(aligned),
        man.get_data(intended_template)
    )
    interdg=results.downgrade()
    intradg = intra_results.downgrade()

    score = 10 - interdg - intradg
    
    display(widgets.HTML(f"10 - {intra_results.downgrade_list()} (intra) - {interdg} (inter) = <h1>{man.uid}: {score}</h1>"))

    fig=None
    
    if intent:
        fig = plotsec(
            man.get_data(intended_template).relocate(transform.pos),
            fig=fig
        )

    if fl:
        fig = plotsec(man.get_data(aligned), fig=fig)
    
    if corr:
        fig = plotsec(
            p23_def[man.uid].create(transform).create_template(Transformation(
                transform.pos,
                man.get_data(corrected_template)[0].att
            )), 
            fig=fig
        )

    if fig:
        display(go.FigureWidget(fig.data, fig.layout))

    if inter:
        display("Inter Element Summary")
        display(results.downgrade_df())

    if intra:
        display(intra_results[el.uid].results.downgrade_df())

man=widgets.IntSlider(min=1, max=17, value=1, step=1)
fl = widgets.Checkbox(True, description="Plot Flown")
intent = widgets.Checkbox(False, description="Plot Intended")
corr = widgets.Checkbox(False, description="Plot Corrected")
inter = widgets.Checkbox(False, description="Inter Summary")
intra = widgets.Checkbox(False, description="Intra Summary")
el=widgets.IntSlider(min=1, max=20, value=1, step=1)

controls = widgets.HBox(children=[man, fl, intent, corr, inter, intra, el])
results = widgets.interactive_output(scoreman, dict(man=man, fl=fl, intent=intent, corr=corr, inter=inter, intra=intra, el=el))

widgets.VBox([
    controls,
    results
])



In [15]:
from tkinter import W
from geometry import PZ, Point, Coord, P0, Quaternion, PY
import plotly.graph_objects as go
import json
from flightplotting.traces import trace3d
import flightplotting.templates
import plotly.express as px
from flightanalysis import Loop

man = intended[0]
el = man.elements[0]

#TODO this is a faff, add manoeuvre name to the ElDef name on creation to remove two of these lines
flown_man = man.get_data(aligned) 
template_man = man.get_data(intended_template)

flown_el = el.get_data(flown_man)
template_el = el.get_data(template_man).relocate(flown_el.pos[0])

flown_lc =  el.setup_analysis_state(flown_el, template_el)
template_lc =  el.setup_analysis_state(template_el, template_el)

fig = plotsec(flown_lc, nmodels=5)
plotsec(template_lc, nmodels=5, color="red", fig=fig).show()

mdf = el.intra_scoring.measuredf(el, flown_lc, template_lc)

results = el.intra_scoring.dgs(mdf)

print(results.downgrade())
print(results.downgrade_df())



0.5
      speed  radius roll_angle     track
0  0.010981  0.2021   0.390487  0.009082
1  0.000252           0.076501  0.418630
2  0.000328           0.002947  0.004223
3   0.04164           0.004299  0.009822
4  0.000045           0.000774  0.002984
5                     0.008289  0.005151
6                      0.16848  0.003388
7                               0.001573
8                               0.033483


In [12]:
from json import dump
name = "rolling_loop"
#flown_lc.to_csv(f"examples/{name}_analysis/flown_{name}.csv")
#template_lc.to_csv(f"examples/{name}_analysis/template_{name}.csv")
#with open(f"examples/{name}_analysis/{name}_element.json", "w") as f:
#    dump(el.to_dict(), f)
